In [2]:
import serial
import time
from datetime import datetime
from openpyxl import Workbook, load_workbook

# Configurações
PORT = 'COM11'  # Substitua pela porta correta do seu Arduino
BAUD_RATE = 9600

# Configurações do controle de temperatura
SETPOINT = 80.0  # Define o setpoint da temperatura
HISTERESE = 2.0  # Define a faixa de histerese

# Nome do arquivo
file_name = 'calibracao_dados_arduino.xlsx'

def verifica_setpoint(temperatura_corrigida):
    """
    Função para verificar o status do setpoint:
    Retorna:
    - Status do Setpoint: 'Não chegou ainda' ou 'Já passou'
    - Acionamento da Resistência: 1 (ligada) ou 0 (desligada)
    """
    if temperatura_corrigida < SETPOINT - HISTERESE:
        return "Não chegou ainda", 1  # Resistência ligada (1) quando abaixo do setpoint
    elif temperatura_corrigida > SETPOINT + HISTERESE:
        return "Já passou", 0  # Resistência desligada (0) quando acima do setpoint
    else:
        return "No Setpoint", 0  # Resistência desligada (0) quando dentro do setpoint

def configurar_conexao_serial(port, baud_rate):
    try:
        return serial.Serial(port, baud_rate)
    except serial.SerialException as e:
        print(f"Erro ao abrir a porta serial: {e}")
        return None

def carregar_arquivo_excel(file_name):
    try:
        return load_workbook(file_name)
    except FileNotFoundError:
        return Workbook()

def criar_aba(wb, sheet_index):
    sheet_name = f'Teste_{sheet_index}'
    return wb.create_sheet(title=sheet_name)

def processar_dados(ser, ws):
    while True:
        try:
            linha = ser.readline().decode('utf-8').strip()
            if linha and "Temp. Bruta" in linha:
                print(f"Recebido: {linha}")
                partes = linha.split(',')
                temp_bruta = partes[0].split(':')[1].strip().split()[0]  # Temperatura Bruta
                temp_corrigida = float(partes[1].split(':')[1].strip().split()[0])  # Temperatura Corrigida
                temp_ambiente = partes[2].split(':')[1].strip().split()[0]  # Temperatura Ambiente
                
                hora_atual = datetime.now().strftime('%H:%M')
                
                status_setpoint, resistencia_status = verifica_setpoint(temp_corrigida)
                
                ws.append([hora_atual, temp_bruta, temp_corrigida, temp_ambiente, status_setpoint, resistencia_status])
                
                print(f"Hora: {hora_atual}, Temp Bruta: {temp_bruta} C, Temp Corrigida: {temp_corrigida} C, Temp Ambiente: {temp_ambiente} C, Status: {status_setpoint}, Resistência: {resistencia_status}")
        except Exception as e:
            print(f"Erro ao ler dados: {e}")

def main():
    ser = configurar_conexao_serial(PORT, BAUD_RATE)
    if ser:
        time.sleep(2)  # Espera o Arduino inicializar
        
        wb = carregar_arquivo_excel(FILE_NAME)
        sheet_index = len(wb.sheetnames) + 1 if wb else 1
        ws = criar_aba(wb, sheet_index)
        ws.append(['Hora', 'Temperatura Bruta (C)', 'Temperatura Corrigida (C)', 'Temperatura Ambiente (C)', 'Status do Setpoint', 'Acionamento da Resistência (1=Ligada, 0=Desligada)'])
        
        print(f"Conectado à porta {PORT}. Começando a coletar dados...")
        
        processar_dados(ser, ws)
        
        wb.save(FILE_NAME)
        ser.close()

if __name__ == "__main__":
    main()

Conectado à porta COM11. Começando a coletar dados...
Recebido: Temp. Bruta: 0.00 C, Temp. Corrigida: -2.23 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 0.00 C, Temp Corrigida: -2.23 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 30.75 C, Temp. Corrigida: 26.61 C, Temp. Ambiente: 37.15 C
Hora: 10:06, Temp Bruta: 30.75 C, Temp Corrigida: 26.61 C, Temp Ambiente: 37.15 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 31.75 C, Temp. Corrigida: 27.55 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 31.75 C, Temp Corrigida: 27.55 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 31.75 C, Temp. Corrigida: 27.55 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 31.75 C, Temp Corrigida: 27.55 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 31.75 C, Temp. Corrigida: 27.55 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 31.75 C, Temp Cor

Recebido: Temp. Bruta: 33.00 C, Temp. Corrigida: 28.72 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.00 C, Temp Corrigida: 28.72 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 32.50 C, Temp. Corrigida: 28.25 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 32.50 C, Temp Corrigida: 28.25 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 32.75 C, Temp. Corrigida: 28.49 C, Temp. Ambiente: 38.61 C
Hora: 10:06, Temp Bruta: 32.75 C, Temp Corrigida: 28.49 C, Temp Ambiente: 38.61 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 32.75 C, Temp. Corrigida: 28.49 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 32.75 C, Temp Corrigida: 28.49 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.00 C, Temp. Corrigida: 28.72 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.00 C, Temp Corrigida: 28.72 C, Temp Ambiente: 39.10 C, Status: Não

Recebido: Temp. Bruta: 32.75 C, Temp. Corrigida: 28.49 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 32.75 C, Temp Corrigida: 28.49 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.25 C, Temp. Corrigida: 28.96 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.25 C, Temp Corrigida: 28.96 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 32.75 C, Temp. Corrigida: 28.49 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 32.75 C, Temp Corrigida: 28.49 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.50 C, Temp. Corrigida: 29.19 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.50 C, Temp Corrigida: 29.19 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.00 C, Temp. Corrigida: 28.72 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.00 C, Temp Corrigida: 28.72 C, Temp Ambiente: 39.10 C, Status: Não

Recebido: Temp. Bruta: 32.75 C, Temp. Corrigida: 28.49 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 32.75 C, Temp Corrigida: 28.49 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.00 C, Temp. Corrigida: 28.72 C, Temp. Ambiente: 39.59 C
Hora: 10:06, Temp Bruta: 33.00 C, Temp Corrigida: 28.72 C, Temp Ambiente: 39.59 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.25 C, Temp. Corrigida: 28.96 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.25 C, Temp Corrigida: 28.96 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.00 C, Temp. Corrigida: 28.72 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.00 C, Temp Corrigida: 28.72 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.25 C, Temp. Corrigida: 28.96 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.25 C, Temp Corrigida: 28.96 C, Temp Ambiente: 39.10 C, Status: Não

Recebido: Temp. Bruta: 33.00 C, Temp. Corrigida: 28.72 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.00 C, Temp Corrigida: 28.72 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.00 C, Temp. Corrigida: 28.72 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.00 C, Temp Corrigida: 28.72 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.50 C, Temp. Corrigida: 29.19 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.50 C, Temp Corrigida: 29.19 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.25 C, Temp. Corrigida: 28.96 C, Temp. Ambiente: 39.10 C
Hora: 10:06, Temp Bruta: 33.25 C, Temp Corrigida: 28.96 C, Temp Ambiente: 39.10 C, Status: Não chegou ainda, Resistência: 1
Recebido: Temp. Bruta: 33.00 C, Temp. Corrigida: 28.72 C, Temp. Ambiente: 39.10 C
Hora: 10:07, Temp Bruta: 33.00 C, Temp Corrigida: 28.72 C, Temp Ambiente: 39.10 C, Status: Não

...

Hora: 12:10, Temp Bruta: 89.25 C, Temp Corrigida: 81.48 C, Temp Ambiente: 29.81 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 88.75 C, Temp. Corrigida: 81.01 C, Temp. Ambiente: 31.28 C
Hora: 12:10, Temp Bruta: 88.75 C, Temp Corrigida: 81.01 C, Temp Ambiente: 31.28 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.00 C, Temp. Corrigida: 81.25 C, Temp. Ambiente: 30.30 C
Hora: 12:10, Temp Bruta: 89.00 C, Temp Corrigida: 81.25 C, Temp Ambiente: 30.30 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 88.75 C, Temp. Corrigida: 81.01 C, Temp. Ambiente: 30.79 C
Hora: 12:10, Temp Bruta: 88.75 C, Temp Corrigida: 81.01 C, Temp Ambiente: 30.79 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 88.50 C, Temp. Corrigida: 80.78 C, Temp. Ambiente: 29.81 C
Hora: 12:10, Temp Bruta: 88.50 C, Temp Corrigida: 80.78 C, Temp Ambiente: 29.81 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.50 C, Temp. Corrigida: 81.72 C, Temp. Ambiente: 29.

Recebido: Temp. Bruta: 89.50 C, Temp. Corrigida: 81.72 C, Temp. Ambiente: 30.30 C
Hora: 12:10, Temp Bruta: 89.50 C, Temp Corrigida: 81.72 C, Temp Ambiente: 30.30 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.00 C, Temp. Corrigida: 81.25 C, Temp. Ambiente: 30.30 C
Hora: 12:10, Temp Bruta: 89.00 C, Temp Corrigida: 81.25 C, Temp Ambiente: 30.30 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.50 C, Temp. Corrigida: 81.72 C, Temp. Ambiente: 29.81 C
Hora: 12:10, Temp Bruta: 89.50 C, Temp Corrigida: 81.72 C, Temp Ambiente: 29.81 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.50 C, Temp. Corrigida: 81.72 C, Temp. Ambiente: 30.79 C
Hora: 12:10, Temp Bruta: 89.50 C, Temp Corrigida: 81.72 C, Temp Ambiente: 30.79 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.25 C, Temp. Corrigida: 81.48 C, Temp. Ambiente: 30.30 C
Hora: 12:10, Temp Bruta: 89.25 C, Temp Corrigida: 81.48 C, Temp Ambiente: 30.30 C, Status: No Setpoint, Resistênci

Recebido: Temp. Bruta: 89.50 C, Temp. Corrigida: 81.72 C, Temp. Ambiente: 30.79 C
Hora: 12:10, Temp Bruta: 89.50 C, Temp Corrigida: 81.72 C, Temp Ambiente: 30.79 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.25 C, Temp. Corrigida: 81.48 C, Temp. Ambiente: 30.79 C
Hora: 12:10, Temp Bruta: 89.25 C, Temp Corrigida: 81.48 C, Temp Ambiente: 30.79 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.25 C, Temp. Corrigida: 81.48 C, Temp. Ambiente: 30.79 C
Hora: 12:10, Temp Bruta: 89.25 C, Temp Corrigida: 81.48 C, Temp Ambiente: 30.79 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.50 C, Temp. Corrigida: 81.72 C, Temp. Ambiente: 30.79 C
Hora: 12:10, Temp Bruta: 89.50 C, Temp Corrigida: 81.72 C, Temp Ambiente: 30.79 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.75 C, Temp. Corrigida: 81.95 C, Temp. Ambiente: 30.30 C
Hora: 12:10, Temp Bruta: 89.75 C, Temp Corrigida: 81.95 C, Temp Ambiente: 30.30 C, Status: No Setpoint, Resistênci

Recebido: Temp. Bruta: 89.25 C, Temp. Corrigida: 81.48 C, Temp. Ambiente: 23.46 C
Hora: 12:10, Temp Bruta: 89.25 C, Temp Corrigida: 81.48 C, Temp Ambiente: 23.46 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.75 C, Temp. Corrigida: 81.95 C, Temp. Ambiente: 23.46 C
Hora: 12:10, Temp Bruta: 89.75 C, Temp Corrigida: 81.95 C, Temp Ambiente: 23.46 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.25 C, Temp. Corrigida: 81.48 C, Temp. Ambiente: 22.48 C
Hora: 12:10, Temp Bruta: 89.25 C, Temp Corrigida: 81.48 C, Temp Ambiente: 22.48 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.50 C, Temp. Corrigida: 81.72 C, Temp. Ambiente: 22.48 C
Hora: 12:10, Temp Bruta: 89.50 C, Temp Corrigida: 81.72 C, Temp Ambiente: 22.48 C, Status: No Setpoint, Resistência: 0
Recebido: Temp. Bruta: 89.25 C, Temp. Corrigida: 81.48 C, Temp. Ambiente: 23.46 C
Hora: 12:10, Temp Bruta: 89.25 C, Temp Corrigida: 81.48 C, Temp Ambiente: 23.46 C, Status: No Setpoint, Resistênci

KeyboardInterrupt: 

In [ ]:
import serial
import time
from datetime import datetime
from openpyxl import Workbook, load_workbook

# Configurações
PORT = 'COM11'  # Substitua pela porta correta do seu Arduino
BAUD_RATE = 9600

# Configurações do controle de temperatura
SETPOINT = 80.0  # Define o setpoint da temperatura
HISTERESE = 2.0  # Define a faixa de histerese

# Nome do arquivo
FILE_NAME = 'calibracao_dados_arduino.xlsx'

def verifica_setpoint(temperatura_corrigida):
    """
    Função para verificar o status do setpoint:
    Retorna:
    - Status do Setpoint: 'Não chegou ainda' ou 'Já passou'
    - Acionamento da Resistência: 1 (ligada) ou 0 (desligada)
    """
    if temperatura_corrigida < SETPOINT - HISTERESE:
        return "Não chegou ainda", 1  # Resistência ligada (1) quando abaixo do setpoint
    elif temperatura_corrigida > SETPOINT + HISTERESE:
        return "Já passou", 0  # Resistência desligada (0) quando acima do setpoint
    else:
        return "No Setpoint", 0  # Resistência desligada (0) quando dentro do setpoint

def configurar_conexao_serial(port, baud_rate):
    try:
        return serial.Serial(port, baud_rate)
    except serial.SerialException as e:
        print(f"Erro ao abrir a porta serial: {e}")
        return None

def carregar_arquivo_excel(file_name):
    try:
        return load_workbook(file_name)
    except FileNotFoundError:
        return Workbook()

def criar_aba(wb, sheet_index):
    sheet_name = f'Teste_{sheet_index}'
    return wb.create_sheet(title=sheet_name)

def processar_dados(ser, ws):
    while True:
        try:
            linha = ser.readline().decode('utf-8').strip()
            if linha and "Temp. Bruta" in linha:
                print(f"Recebido: {linha}")
                partes = linha.split(',')
                temp_bruta = partes[0].split(':')[1].strip().split()[0]  # Temperatura Bruta
                temp_corrigida = float(partes[1].split(':')[1].strip().split()[0])  # Temperatura Corrigida
                temp_ambiente = partes[2].split(':')[1].strip().split()[0]  # Temperatura Ambiente
                
                hora_atual = datetime.now().strftime('%H:%M')
                
                status_setpoint, resistencia_status = verifica_setpoint(temp_corrigida)
                
                ws.append([hora_atual, temp_bruta, temp_corrigida, temp_ambiente, status_setpoint, resistencia_status])
                
                print(f"Hora: {hora_atual}, Temp Bruta: {temp_bruta} C, Temp Corrigida: {temp_corrigida} C, Temp Ambiente: {temp_ambiente} C, Status: {status_setpoint}, Resistência: {resistencia_status}")
        except Exception as e:
            print(f"Erro ao ler dados: {e}")

def main():
    ser = configurar_conexao_serial(PORT, BAUD_RATE)
    if ser:
        time.sleep(2)  # Espera o Arduino inicializar
        
        wb = carregar_arquivo_excel(FILE_NAME)
        sheet_index = len(wb.sheetnames) + 1 if wb else 1
        ws = criar_aba(wb, sheet_index)
        ws.append(['Hora', 'Temperatura Bruta (C)', 'Temperatura Corrigida (C)', 'Temperatura Ambiente (C)', 'Status do Setpoint', 'Acionamento da Resistência (1=Ligada, 0=Desligada)'])
        
        print(f"Conectado à porta {PORT}. Começando a coletar dados...")
        
        processar_dados(ser, ws)
        
        wb.save(FILE_NAME)
        ser.close()

if __name__ == "__main__":
    main()

In [2]:
import pandas as pd

# Nome do arquivo CSV
csv_file = 'DATALOG-2.CSV'  # Substitua pelo seu arquivo CSV

# Nome do arquivo Excel de saída
excel_file = 'dados-2.xlsx'

# Leitura do arquivo CSV
df = pd.read_csv(csv_file)

# Salvar em formato Excel (.xlsx)
df.to_excel(excel_file, index=False)

print(f"Arquivo {csv_file} convertido com sucesso para {excel_file}")


C:\Users\bruno\AppData\Local\Temp\ipykernel_18300\1017284841.py:13: UserWarning: Pandas requires version '3.0.5' or newer of 'xlsxwriter' (version '3.0.3' currently installed).
  df.to_excel(excel_file, index=False)


Arquivo DATALOG-2.CSV convertido com sucesso para dados-2.xlsx
